To use the GATE Cloud API, `POST` the data you want to process to the endpoint URL you copied from the GATE Cloud details page. The `Content-Type` header must be set to the type of data, e.g. `text/plain`, `application/xml`, `application/pdf`, etc.

Authentication uses the standard [HTTP Basic authentication](https://en.wikipedia.org/wiki/Basic_access_authentication) mechanism, using your API key ID as the username and the API key password as the password - do not use your `cloud.gate.ac.uk` login username and password, these will not work.

To override the default annotation selectors you can use the `annotations` parameter on the end of the URL, for example

```
https://cloud-api.gate.ac.uk/process-document/annie-named-entity-recognizer?annotations=:Person&annotations=:Location
```

Remember the available selectors can be found under the "annotation details" button on the pipeline info page.

In [ ]:
import requests

response = requests.post('https://cloud-api.gate.ac.uk/process-document/annie-named-entity-recognizer',
                         # auth=('keyId', 'keyPassword'), # uncomment for authentication
                         params={'annotations':[':Person', ':Location', ':Sentence']},
                         data='Ian lives in Sheffield'.encode('UTF-8'),
                         headers={'Content-Type':'text/plain'})

By default the API will return its response in JSON, and you can parse this to extract the annotations.  The `"indices"` are character positions relative to the `"text"` property of the response, which may not be exactly the same as the original text you sent in.

In [ ]:
j = response.json()
txt = j['text']
for ann_type, anns in j['entities'].items():
  print(ann_type)
  for a in anns:
    start, end = a['indices']
    print(f'- {txt[start:end]} ({start}:{end})')

Each call to the API returns useful information about your 24-hour quota in custom HTTP response headers:

 - `X-GATE-Request-Cost` - how many "units" of quota this call consumed
 - `X-GATE-Remaining-Quota` - how much quota remains after this call, until...
 - `X-GATE-Quota-Reset` - quota reset time, expressed as the number of seconds from the time of this call

and similarly about the rate limit (implemented in terms of a maximum number of requests within any five minute window):

 - `X-GATE-Rate-Limit-Calls` - how many calls remain in the current rate limit window after this call
 - `X-GATE-Rate-Limit-Reset` - how many seconds until the end of the window

In [ ]:
for (k, v) in response.headers.items():
  print(f"{k}: {v}")